In [27]:
import numpy as np 
import matplotlib.pyplot as plt 
import pandas as pd 
import blimpy as bl 
import os
%matplotlib inline

In [2]:
df = pd.read_csv('/datax/scratch/benjb/bl_nearby_stars/star_cadences_catalog_no_band.csv')
arr = np.transpose(np.array([
    df['Distance'].values, 
    df['Cadence ID'].values, 
    df['.h5 path'].values], 
    dtype=str))
u = np.unique(arr, axis=0)
print(len(arr))
print(len(u))

282858
237168


In [ ]:
files_per_cadence = []

for i, cadence_id in enumerate(np.unique(df['Cadence ID'].values)):
    dist_list = df['Distance'].values[np.where(df['Cadence ID'].values == cadence_id)[0]]
    target_list = df['Target'].values[np.where(df['Cadence ID'].values == cadence_id)[0]]
    files_per_cadence.append(len(target_list))

In [55]:
from collections import Counter

def find_most_common(lst):
    counts = Counter(lst)
    largest_value = max(counts.values())
    modes = [k for k, n in counts.items() if n == largest_value]
    return sorted(modes)

a = ['HIP62079', 'HIP62079', 'HIP70857', 'HIP70857', 'HIP70857', 'HIP54.1']
print(find_most_common(a))

['HIP70857']


In [58]:
new_arr = []
dfd = pd.read_csv('/datax/scratch/benjb/bl_nearby_stars/BL_star_targets_all_sky.csv')
dvec = dfd['dist (pc)'].values
dnames = dfd['Name'].values

for i in range(len(df['Cadence ID'].values)//6):
    cadence_id_list = df['Cadence ID'].values[6*i:6*i+6]
    ucid = np.unique(cadence_id_list)
    if len(ucid) > 1:
        print(f'Bad counting assumption! Check cadence IDs {ucid}.')
        break
    h5_list = df['.h5 path'].values[6*i:6*i+6]
    f_list = df['Frequency'].values[6*i:6*i+6]
    # pull target names from filenames (not from df['Target'].values)
    target_list = []
    for file in h5_list:
        basename = os.path.basename(file)
        start = 'guppi'
        s = (basename.split(start))[1][13:]
        target = (s.split('_'))[0]
        #print(target, target.upper())
        target_list.append(target.upper())
    mode_target = find_most_common(target_list)
    if len(mode_target) > 1:
        print(f'ABABAB cadence detected! Check both targets: {mode_target}')
    for target in mode_target:
        if target in dnames:
            dist = dvec[np.where(dnames==target)[0][0]]
        else:
            print('Target not in nearby star sample. Continuing ...')
            continue
        for i in range(6):
            vec = np.array([target, dist, cadence_id_list[i], f_list[i], h5_list[i]])
            new_arr.append(vec)

Target not in nearby star sample. Continuing ...
Target not in nearby star sample. Continuing ...
ABABAB cadence detected! Check both targets: ['HIP24680', 'HIP25110']
Target not in nearby star sample. Continuing ...
Target not in nearby star sample. Continuing ...
ABABAB cadence detected! Check both targets: ['HIP24680', 'HIP25110']
Target not in nearby star sample. Continuing ...
ABABAB cadence detected! Check both targets: ['HIP24680', 'HIP25110']
Target not in nearby star sample. Continuing ...
ABABAB cadence detected! Check both targets: ['HIP24680', 'HIP25110']
Target not in nearby star sample. Continuing ...
ABABAB cadence detected! Check both targets: ['HIP24680', 'HIP25110']
Target not in nearby star sample. Continuing ...
ABABAB cadence detected! Check both targets: ['HIP24680', 'HIP25110']
Target not in nearby star sample. Continuing ...
ABABAB cadence detected! Check both targets: ['HIP24680', 'HIP25110']
Target not in nearby star sample. Continuing ...
ABABAB cadence detec

In [82]:
new_arr = np.array(new_arr)
idxs = np.where(new_arr[:,1].astype(float) <= 5.1)[0]
print(idxs)
new_arr_close = new_arr[idxs]
a = np.transpose([new_arr_close[:,2], new_arr_close[:,4]])
b = np.transpose([new_arr_close[:,0], new_arr_close[:,1], new_arr_close[:,2], new_arr_close[:,4]])
print(len(a))
print(len(np.unique(a, axis=0)))
print(len(np.unique(b, axis=0)))

[     0      1      2 ... 281739 281740 281741]
12558
10242
10242


In [85]:
a = np.transpose([new_arr[:,2], new_arr[:,4]])
b = np.transpose([new_arr[:,0], new_arr[:,1], new_arr[:,2], new_arr[:,4]])
print(len(a))
a, ac = np.unique(a, axis=0, return_counts=True)
b, bc = np.unique(b, axis=0, return_counts=True)
print(ac[:10])
print(bc[:10])

281742
[1 1 1 1 1 1 1 1 1 1]
[1 1 1 1 1 1 1 1 1 1]


In [90]:
for i in range(len(ac)):
    if ac[i] != bc[i]:
        print(f'Error at index {i}!')
        break
print(ac[:i+5])
print(bc[:i+5])

Error at index 12!
[1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
[1 1 1 1 1 1 1 1 1 1 1 1 2 2 2 2 2]


In [91]:
print(a[0])
print(b[0])

# PICK UP HERE 01/07/25: track down why len(np.unique(a, axis=0)) != len(np.unique(b, axis=0)).
# It is probably because both targets of a single cadence are in the nearby star sample.
# Hence: two targets for a single cadence ID.
# Double-check, though!

['1000'
 '/datag/pipeline/AGBT16A_999_136/holding/spliced_blc02030405_2bit_guppi_57487_62349_HIP9487_0003.gpuspec.0000.h5']
['GJ1002' '4.69' '12847'
 '/datag/pipeline/AGBT16B_999_82/collate/spliced_blc0001020304050607_guppi_57725_01108_GJ1002_0002.gpuspec.0000.h5']


In [83]:
df0 = pd.DataFrame(data=np.unique(b, axis=0), columns=['Target', 'Distance', 'Cadence ID', '.h5 path'])
df0.to_csv('/datax/scratch/benjb/bl_nearby_stars/unique_star_cadences_catalog_within_5.1_pc_no_band.csv', index=False) 

In [10]:
arr2 = arr[:,1:]
u2, c2 = np.unique(arr2, axis=0, return_counts=True)
for i in u2[np.where(c2!=1)[0]]:
    print(i)

['1001'
 '/datag/pipeline/AGBT16A_999_136/holding/spliced_blc02030405_2bit_guppi_57487_62676_HIP9487_OFF_0004.gpuspec.0000.h5']
['1001'
 '/datag/pipeline/AGBT16A_999_136/holding/spliced_blc02030405_2bit_guppi_57487_63003_HIP9487_0005.gpuspec.0000.h5']
['1001'
 '/datag/pipeline/AGBT16A_999_136/holding/spliced_blc02030405_2bit_guppi_57487_63330_HIP9487_OFF_0006.gpuspec.0000.h5']
['1001'
 '/datag/pipeline/AGBT16A_999_136/holding/spliced_blc02030405_2bit_guppi_57487_63657_HIP9487_0007.gpuspec.0000.h5']
['1001'
 '/datag/pipeline/AGBT16A_999_136/holding/spliced_blc02030405_2bit_guppi_57487_63984_HIP9487_OFF_0008.gpuspec.0000.h5']
['1001'
 '/datag/pipeline/AGBT16A_999_136/holding/spliced_blc02030405_2bit_guppi_57487_64373_HIP9829_0009.gpuspec.0000.h5']
['10034'
 '/datag/pipeline/AGBT16B_999_25/collate/spliced_blc0001020304050607_guppi_57650_68107_Hip65026_0003.gpuspec.0000.h5']
['10034'
 '/datag/pipeline/AGBT16B_999_25/collate/spliced_blc0001020304050607_guppi_57650_68456_Hip63894_0004.gpuspe

In [9]:
print(u[np.where(u[:,1]=='1001')[0]])

[['23.1' '1001'
  '/datag/pipeline/AGBT16A_999_136/holding/spliced_blc02030405_2bit_guppi_57487_62676_HIP9487_OFF_0004.gpuspec.0000.h5']
 ['23.1' '1001'
  '/datag/pipeline/AGBT16A_999_136/holding/spliced_blc02030405_2bit_guppi_57487_63003_HIP9487_0005.gpuspec.0000.h5']
 ['23.1' '1001'
  '/datag/pipeline/AGBT16A_999_136/holding/spliced_blc02030405_2bit_guppi_57487_63330_HIP9487_OFF_0006.gpuspec.0000.h5']
 ['23.1' '1001'
  '/datag/pipeline/AGBT16A_999_136/holding/spliced_blc02030405_2bit_guppi_57487_63657_HIP9487_0007.gpuspec.0000.h5']
 ['23.1' '1001'
  '/datag/pipeline/AGBT16A_999_136/holding/spliced_blc02030405_2bit_guppi_57487_63984_HIP9487_OFF_0008.gpuspec.0000.h5']
 ['23.1' '1001'
  '/datag/pipeline/AGBT16A_999_136/holding/spliced_blc02030405_2bit_guppi_57487_64373_HIP9829_0009.gpuspec.0000.h5']
 ['42.6' '1001'
  '/datag/pipeline/AGBT16A_999_136/holding/spliced_blc02030405_2bit_guppi_57487_62676_HIP9487_OFF_0004.gpuspec.0000.h5']
 ['42.6' '1001'
  '/datag/pipeline/AGBT16A_999_136/ho

In [7]:
for i in np.random.choice(len(arr), 10):
    print(arr[i])

['26.1' '42167'
 '/datag/pipeline/AGBT19A_999_60/blc60/blc60_guppi_58663_69254_HIP22588_0111.gpuspec.0000.h5']
['27.3' '42741'
 '/datag/pipeline/AGBT19A_999_65/blc63/blc63_guppi_58678_22492_HIP80179_0110.gpuspec.0000.h5']
['16.2' '420691'
 '/datag/pipeline/AGBT23B_999_03/blc51_blp11/blc51_guppi_60272_82833_HIP91608_0115.rawspec.0000.h5']
['20.3' '40584'
 '/datag/pipeline/AGBT19A_999_47/blc54/blc54_guppi_58628_61077_HIP108156_0034.gpuspec.0000.h5']
['44.8' '418755'
 '/datag/pipeline/AGBT23A_999_39/blc06_blp06/blc06_guppi_60226_46780_HIP20553_0071.rawspec.0000.h5']
['16.6' '49222'
 '/datag/pipeline/AGBT19B_999_19/blp26/blc26_guppi_58737_32853_HIP11452_0042.gpuspec.0000.h5']
['20.8' '420665'
 '/datag/pipeline/AGBT23B_999_03/blc65_blp25/blc65_guppi_60272_54123_HIP97295_0023.rawspec.0000.h5']
['14.5' '424381'
 '/datag/pipeline/AGBT23A_999_46/blc63_blp23/blc63_guppi_60241_04523_HIP70497_0023.rawspec.0000.h5']
['19.9' '16012'
 '/datag/pipeline/AGBT17A_999_38/holding/spliced_blc000102030405060

In [21]:
u5 = u[np.where(u[:,0].astype(float) <= 5.1)[0]]
u5u = np.unique(u5[:,1], axis=0)
print(len(u5u))

249


In [22]:
249/6

41.5

In [20]:
for i in np.random.choice(len(u5), 20):
    print(u5[i])

['4.38' '25491'
 '/datag/pipeline/AGBT18A_999_118/collate/spliced_blc00010203040506o7o0111213141516o7o021222324252627_guppi_58326_83555_HIP60527_0024.gpuspec.0000.h5']
['3.57' '420941'
 '/datag/pipeline/AGBT23B_999_08/blc07_blp07/blc07_guppi_60277_25288_GJ15B_0074.rawspec.0000.h5']
['5.04' '36561'
 '/datag/pipeline/AGBT18B_999_95/blc56/blc56_guppi_58494_73326_GJ873_0088.gpuspec.0000.h5']
['3.71' '353139'
 '/datag/pipeline/AGBT21A_996_51/blc15/blc15_guppi_59414_30982_HIP5830_0130.rawspec.0000.h5']
['3.85' '421558'
 '/datag/pipeline/AGBT23B_999_14/blc51_blp11/blc51_guppi_60291_04795_HIP13871_0020.rawspec.0000.h5']
['3.75' '9747'
 '/datag/pipeline/AGBT16B_999_20/holding/spliced_blc0001020304050607_guppi_57635_50794_Hip34978_0048.gpuspec.0000.h5']
['4.54' '39721'
 '/datag/pipeline/AGBT19A_999_38/blc55/blc55_guppi_58605_16389_GJ1245B_0023.gpuspec.0000.h5']
['2.54' '34998'
 '/datag/pipeline/AGBT18B_999_73/blp23/blc53_guppi_58454_38368_GJ411_0051.gpuspec.0000.h5']
['3.45' '29700'
 '/datag/pip

In [15]:
10296/6

1716.0

In [17]:
282858/10600

26.684716981132077